In [4]:
import sys, os, glob
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from pl_rec_export.src.pupil_labs.pikit.recording import Recording
from pl_rec_export.src.pupil_labs.rec_export.explib.fixation_detector import optic_flow_correction
from pl_rec_export.src.pupil_labs.rec_export.explib.fixation_detector import helpers

INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [14]:
rec_folder = '/Users/jyeon/Documents/GitHub/calibrate_fixations/data/testing_opticflow/2024-05-01_17-14-59-*******'
rec = Recording(rec_folder)

In [15]:
# gaze processes
progress = None
time_axis, timestamps, gaze_distorted, gaze_rectified, gaze_normalized = helpers.get_gaze_from_recording(rec_folder, progress)

gaze_normalized_x, resampled_time_axis = helpers.resample_linearly(
        gaze_normalized[:, 0], time_axis
    )
gaze_normalized_y, _ = helpers.resample_linearly(gaze_normalized[:, 1], time_axis)
gaze_distorted_x, _ = helpers.resample_linearly(gaze_distorted[:, 0], time_axis)
gaze_distorted_y, _ = helpers.resample_linearly(gaze_distorted[:, 1], time_axis)


INFO:pl_rec_export.src.pupil_labs.pikit.lib.video_timestamp_reader:mp4 frame time reader for <WorldPart number=1, start_epoch_ns=1714608905186101108, offset_ns=5343101108, n_timestamps=3015, n_samples=3015, is_valid_part=True>


In [16]:
# get optic flow
optic_flow_vectors = optic_flow_correction.load_optic_flow_vectors(
    rec_folder, use_existing=False, progress=progress
)


INFO:pl_rec_export.src.pupil_labs.rec_export.explib.fixation_detector.optic_flow_correction:Calculating optic flow vectors for /Users/jyeon/Documents/GitHub/calibrate_fixations/data/testing_opticflow/2024-05-01_17-14-59-48a4490e
INFO:pl_rec_export.src.pupil_labs.rec_export.explib.fixation_detector.optic_flow_correction:Calculating optic flow vectors.
INFO:pl_rec_export.src.pupil_labs.pikit.lib.video_timestamp_reader:mp4 file time reader for <WorldPart number=1, start_epoch_ns=1714608905186101108, offset_ns=5343101108, n_timestamps=3015, n_samples=3015, is_valid_part=True>
INFO:pl_rec_export.src.pupil_labs.pikit.lib.video_timestamp_reader:mp4 frame time reader for <WorldPart number=1, start_epoch_ns=1714608905186101108, offset_ns=5343101108, n_timestamps=3015, n_samples=3015, is_valid_part=True>


Output()

INFO:pl_rec_export.src.pupil_labs.rec_export.explib.fixation_detector.optic_flow_correction:Saving optic flow vectors to /Users/jyeon/Documents/GitHub/calibrate_fixations/data/testing_opticflow/2024-05-01_17-14-59-48a4490e/optic_flow_vectors.npz


In [19]:
# get velocity
# get camera matrix and distortion coefficients for this recording
rec = Recording(rec_folder)
camera_matrix = rec.scene_camera.camera_matrix
distortion_coefficients = rec.scene_camera.distortion_coefficients[0]

# get corrected velocity
velocity = optic_flow_correction.get_corrected_angular_velocity(
    optic_flow_vectors,
    resampled_time_axis,
    gaze_distorted,
    gaze_normalized,
    camera_matrix,
    distortion_coefficients,
)


TypeError: _get_estimated_next_points() takes 2 positional arguments but 4 were given